In [ ]:
%%capture
import pandas as pd
!pip install transformers
!pip install sentencepiece
!pip install pytorch_transformers
import torch
from torch.utils.data import TensorDataset, DataLoader
import torch.optim as optim
import tensorflow as tf
tf.config.run_functions_eagerly(True)
import tensorflow_datasets as tfds
import numpy as np
import re
from keras.preprocessing.sequence import pad_sequences
from time import time
import IPython
from IPython.display import clear_output 
import matplotlib.pyplot as plt
import pandas as pd
%matplotlib inline

In [ ]:
data = pd.read_csv('Emotion_final.csv')
data

Text  Emotion
0                                i didnt feel humiliated  sadness
1      i can go from feeling so hopeless to so damned...  sadness
2       im grabbing a minute to post i feel greedy wrong    anger
3      i am ever feeling nostalgic about the fireplac...     love
4                                   i am feeling grouchy    anger
...                                                  ...      ...
21454               Melissa stared at her friend in dism     fear
21455  Successive state elections have seen the gover...     fear
21456               Vincent was irritated but not dismay     fear
21457  Kendall-Hume turned back to face the dismayed ...     fear
21458                    I am dismayed , but not surpris     fear

[21459 rows x 2 columns]

In [ ]:
from transformers import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-large-uncased' , do_lower_case=True)

In [ ]:
!pip install numpy requests nlpaug
!pip install torch>=1.6.0 transformers>=4.0.0
import nlpaug.augmenter.char as nac
import nlpaug.augmenter.word as naw
import nlpaug.augmenter.sentence as nas
import nlpaug.flow as nafc
from nlpaug.util import Action

     |████████████████████████████████| 399kB 14.1MB/s 


In [ ]:
label_suprise = data[data['Emotion'] == 'anger']
label_suprise['Emotion'].value_counts(normalize = True)
label_love = data[data['Emotion'] == 'fear']
label_love['Emotion'].value_counts(normalize = True)
l = label_suprise['Text'].tolist()
z = label_love['Text'].tolist()
def divide_list(lst , denominator ):
    lol = []
    for x in range(denominator+1):
        globals()['lst%s' % x] = []
        lol.append(globals()['lst%s' % x])
    section = len(lst)//denominator 
    for i in range(len(lst)):
        lol[i//section].append(lst[i])
    return lol
one_label = divide_list(l , 10)
aug = naw.ContextualWordEmbsAug(model_path='bert-base-uncased', action="insert")
for i in range(len(one_label)):
    one_label[i] = aug.augment(one_label[i] , 20)
with open('label_anger.txt', 'w') as filehandle:
    for listitem in one_label:
        filehandle.write('%s\n' % listitem)
zero_label = divide_list(z , 10)
aug = naw.ContextualWordEmbsAug(model_path='bert-base-uncased', action="insert")
for i in range(len(zero_label)):
    zero_label[i] = aug.augment(zero_label[i] , 5)
with open('label_fear.txt', 'w') as filehandle:
    for listitem in zero_label:
        filehandle.write('%s\n' % listitem) 

In [ ]:
flat_list_one = [item for sublist in one_label for item in sublist]
label_flat_one = []
for i in range (len(flat_list_one)):
    label_flat_one.append('anger')
flat_list_zero = [item for sublist in zero_label for item in sublist]
label_flat_zero = []
for i in range (len(flat_list_zero)):
    label_flat_zero.append('fear')
flat_panda_one = pd.DataFrame(list(zip(flat_list_one ,label_flat_one)) , columns=['Text','Emotion'])
flat_panda_zero = pd.DataFrame(list(zip(flat_list_zero ,label_flat_zero)) , columns=['Text','Emotion'])
bigdata = flat_panda_one.append(flat_panda_zero)

In [ ]:
bigdata

Text Emotion
0     im grabbing a minute to post i have feel was g...   anger
1                           i am indeed feeling grouchy   anger
2     i did think, it s the total easiest time of ye...   anger
3     and i feel utterly irritated and rejected with...   anger
4     i already feel like think i fucked up myself t...   anger
...                                                 ...     ...
2647  melissa stared hesitantly at her friend in dre...    fear
2648  successive state representation elections have...    fear
2649           vincent was irritated but yet not dismay    fear
2650  kendall - man hume turned back and to complete...    fear
2651  inside i am all dismayed, disappointed but not...    fear

[5645 rows x 2 columns]

In [ ]:
from IPython.display import HTML
import pandas as pd
import numpy as np
import base64
def create_download_link(df, title = "Download CSV file", filename = "data.csv"):  
    csv = df.to_csv()
    b64 = base64.b64encode(csv.encode())
    payload = b64.decode()
    html = '<a download="{filename}" href="data:text/csv;base64,{payload}" target="_blank">{title}</a>'
    html = html.format(payload=payload,title=title,filename=filename)
    return HTML(html)
create_download_link(bigdata)